In [4]:
import os

os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

In [5]:
from monty.serialization import loadfn, dumpfn

In [5]:
from ase.filters import FrechetCellFilter
from ase.optimize import LBFGS
from pymatgen.io.ase import AseAtomsAdaptor
# from orb_models.forcefield import pretrained
# from orb_models.forcefield.calculator import ORBCalculator
from fairchem.core import pretrained_mlip, FAIRChemCalculator
# from mace.calculators import mace_mp
# from mattersim.forcefield import MatterSimCalculator
# from sevenn.calculator import SevenNetCalculator


cuequivariance or cuequivariance_torch is not available. Cuequivariance acceleration will be disabled.


In [1]:
MODEL = "uma" # "orb" or "uma" or "MPALOE_MatPES" or "seven" or "mattersim"

In [2]:
supercell_size = 10.1

In [7]:
# orb_ff = pretrained.orb_v3_conservative_inf_omat(device="cuda",precision="float32-high")  # or "float32-highest" / "float64
# orb_calc = ORBCalculator(orb_ff, device="cuda")

uma_ff = pretrained_mlip.get_predict_unit("uma-m-1p1", device="cuda")
uma_calc = FAIRChemCalculator(uma_ff, task_name="omat")

# mace_calc = mace_mp(model="MPALOE_MatPES_combined.model", dispersion=False, device='cuda')

# seven_calc = SevenNetCalculator('7net-mf-ompa', modal='omat24')

# mattersim_calc = MatterSimCalculator(device="cuda")

MODELS = {
    # "orb":orb_calc,
    "uma": uma_calc,
    # "seven":seven_calc,
    # "mattersim":mattersim_calc,
    # "eqnorm":eqnorm_calc
    # "MPALOE_MatPES": mace_calc
}

Using float32 for MACECalculator, which is faster but less accurate. Recommended for MD. Use float64 for geometry optimization.
Using head Default out of ['Default']


/home/atshaam/miniconda3/envs/proj_env/lib/python3.11/site-packages/mace/calculators/mace.py:143: UserWarning: Environment variable TORCH_FORCE_NO_WEIGHTS_ONLY_LOAD detected, since the`weights_only` argument was not explicitly passed to `torch.load`, forcing weights_only=False.
  torch.load(f=model_path, map_location=device)


In [8]:
import torch._dynamo
torch._dynamo.config.suppress_errors = True

In [9]:
def relax_structure(structure): # takes in pymatgen structure
    atoms = structure.to_ase_atoms()
    atoms.calc = MODELS[MODEL]
    
    opt = LBFGS(FrechetCellFilter(atoms))# Delete this FrechetCellFilter when doing the defect structures, need FrechetCellFilter when doing competing phases
    opt.run(0.01, 1000)
    
    relaxed_structure = AseAtomsAdaptor.get_structure(atoms)
    energy = atoms.get_potential_energy()

    return relaxed_structure1, energy 

In [10]:
from doped.chemical_potentials import CompetingPhases
from pymatgen.entries.computed_entries import ComputedEntry
from doped.chemical_potentials import CompetingPhasesAnalyzer

In [11]:
calculated_entries = {}

def calc_competing_phase(comp): # Pass in formula of species
    cp = CompetingPhases(composition=comp, extrinsic='Cr', energy_above_hull=0.05)
    
    entries = []
    for entry in cp.entries:
        key =  entry.data['material_id'] + entry.structure.composition.reduced_formula
        
        if key in calculated_entries:
            new_entry = calculated_entries[key]
        else:
            try:
                relaxed_structure, energy = relax_structure(entry.structure)
            except ValueError as e:
                print(f"Skipping structure due to error: {e}")
                continue
            new_entry = ComputedEntry(
                relaxed_structure.composition,
                energy, 
                data = {'material_id':entry.data['material_id']}
            )
            calculated_entries[key] = new_entry 
        entries.append(new_entry)
    return cp, entries 

In [12]:
def calc_competing_phase_analysis(comp, entries):
    
    cpa = CompetingPhasesAnalyzer(composition=comp, entries=entries)
    
    return cpa.chempots, cpa.unstable_host

In [13]:
relaxed_defect = loadfn(f'../../data/{MODEL}/{MODEL}_doped_defect_energies_{supercell_size}A.json')

In [14]:
for key, val in relaxed_defect.items():
    formula = relaxed_defect[key]['formula']
    cp, entries = calc_competing_phase(formula) # do you have to return cp?
    chem_pot, unstable = calc_competing_phase_analysis(formula, entries)
    if 'competing phases' not in relaxed_defect[key]:
        relaxed_defect[key]['competing phases'] = {}
    relaxed_defect[key]['competing phases']['chemical potentials'] = chem_pot
    relaxed_defect[key]['competing phases']['entries'] = entries
    relaxed_defect[key]['competing phases']['unstable'] = unstable

Duplicate entry names found for generated competing phases: AlPO4_Pbca_EaH_0.012!
Duplicate entry names found for generated competing phases: AlPO4_Pbca_EaH_0.012!


       Step     Time          Energy          fmax
LBFGS:    0 12:29:01     -481.976959        0.727715


logm result may be inaccurate, approximate err = 4.726475621142667e-13


LBFGS:    1 12:29:02     -482.100403        0.393811


logm result may be inaccurate, approximate err = 4.700697249847035e-13


...

logm result may be inaccurate, approximate err = 6.029917748364522e-13
logm result may be inaccurate, approximate err = 6.098908539568424e-13


LBFGS:   86 14:17:01     -804.405273        0.007771
       Step     Time          Energy          fmax
LBFGS:    0 14:17:02    -2014.823486        1.075262
LBFGS:    1 14:17:03    -2015.290894        1.063764
LBFGS:    2 14:17:03    -2015.850708        1.021380
LBFGS:    3 14:17:03    -2015.992798        1.011790
LBFGS:    4 14:17:04    -2016.514038        0.934859
LBFGS:    5 14:17:04    -2016.664795        0.918429
LBFGS:    6 14:17:04    -2017.155151        0.861726
LBFGS:    7 14:17:04    -2017.536987        0.819557
LBFGS:    8 14:17:05    -2017.778564        0.790928
LBFGS:    9 14:17:05    -2018.051758        0.798257
LBFGS:   10 14:17:06    -2018.692139        0.950535
LBFGS:   11 14:17:06    -2018.964600        0.800235
LBFGS:   12 14:17:06    -2019.286133        0.790954
LBFGS:   13 14:17:06    -2019.535889        0.784449
LBFGS:   14 14:17:07    -2019.737305        0.776990
LBFGS:   15 14:17:07    -2020.123047        0.759294
LBFGS:   16 14:17:07    -2020.298340        0.74

Duplicate entry names found for generated competing phases: Al2(MoO4)3_NA_EaH_0!


       Step     Time          Energy          fmax
LBFGS:    0 14:19:57     -257.220764        0.341198
LBFGS:    1 14:19:57     -257.234161        0.329063
LBFGS:    2 14:19:57     -257.252045        0.311597
LBFGS:    3 14:19:57     -257.260925        0.295080
LBFGS:    4 14:19:58     -257.287231        0.240300
LBFGS:    5 14:19:58     -257.306580        0.212252
LBFGS:    6 14:19:58     -257.324219        0.230616
LBFGS:    7 14:19:58     -257.335724        0.176578
LBFGS:    8 14:19:58     -257.345459        0.199277
LBFGS:    9 14:19:59     -257.350647        0.142185
LBFGS:   10 14:19:59     -257.353058        0.064255
LBFGS:   11 14:19:59     -257.354187        0.057054
LBFGS:   12 14:19:59     -257.354828        0.039491
LBFGS:   13 14:20:00     -257.355225        0.031989
LBFGS:   14 14:20:00     -257.355560        0.026652
LBFGS:   15 14:20:00     -257.355835        0.029521
LBFGS:   16 14:20:00     -257.355988        0.016421
LBFGS:   17 14:20:00     -257.356079        0.01

Duplicate entry names found for generated competing phases: Al2O3_NA_EaH_0.0322!


In [15]:
dumpfn(relaxed_defect, f'../../data/{MODEL}/{MODEL}_doped_defect_energies_{supercell_size}A.json')